In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import datetime

In [3]:
cad = pd.read_csv('data\\BD_Linhas-de-Transmissão(Cadastro).csv', encoding='latin', sep=';')
med = pd.read_csv('data\\BD_Linhas-de-Transmissão(Documentos de Medição).csv', encoding='latin', sep=';', dtype=object)


med[['Valor teórico',
     'LimInfIntMed.',
     'LimSupIntMed.',
     'ValMed/PosTCont']] = med[['Valor teórico',
     'LimInfIntMed.',
     'LimSupIntMed.',
     'ValMed/PosTCont']].replace({r'\.':'',',':'.'}, regex=True)
     
med[['Valor teórico',
     'LimInfIntMed.',
     'LimSupIntMed.',
     'ValMed/PosTCont']] = med[['Valor teórico',
     'LimInfIntMed.',
     'LimSupIntMed.',
     'ValMed/PosTCont']].astype(float)
     
med[['Equipamento',
     'Ponto medição',
     'Doc.medição']] = med[['Equipamento',
     'Ponto medição',
     'Doc.medição']].astype(int)
     
med['Data'] = pd.to_datetime(med['Data'], dayfirst=True)


cad[['Latitude', 'Longitude']] = cad[['Latitude', 'Longitude']].replace({r'\.':'',',':'.', '#N/D': 'NaN'}, regex=True)

cad[['Latitude', 'Longitude']] = cad[['Latitude', 'Longitude']].astype(float)

cad[['Equipamento', 'Tensão']] = cad[['Equipamento', 'Tensão']].astype(int)

In [4]:
dt = med[['Equipamento', 'Ponto medição', 'Item medição','Denominação', 'Texto']]
dt = dt.rename(columns={'Equipamento':'equip', 'Ponto medição':'ponto', 'Item medição':'item','Denominação':'denom','Texto':'text'})

In [5]:
dt.denom.unique()

array(['ROCADA MECANIZADA', 'ROCADA MANUAL', 'PODA',
       'CABO CONDUTOR (DIR/UNI)', 'Qualificacao do Equipamento',
       'ENTULHO', 'TENTO ROMP-INF/DIR/EXTER(CIRC DIR/UNI)',
       'TENTO ROMP-INF/DIR/EXTER(CIRC ESQ)',
       'TENTO ROMP-MEIO/INTER(CIRC DIR/UNI)',
       'TENTO ROMP-MEIO/INTER(CIRC ESQ)', 'TENTO ROMPIDO(DIR/UNI)',
       'TENTO ROMPIDO(ESQ)', 'CABO PARA-RAIO (DIR/UNI)',
       'CABO PARA-RAIO (ESQ)', 'PROTECAO ANTICORROSIVA',
       'CORROSAO CABO PARA-RAIO (DIR/UNI)', 'PLACA',
       'CORROSAO NA ESTRUTURA', 'BOBINA DE BLOQUEIO (DIR/UNI)',
       'CARGA RUPTURA-INF/DIR/EXTER(CIRC ESQ)',
       'FERRAGENS/CONECTORES CONDUTOR (ESQ)', 'DISTANCIA ATE BURACO',
       'BASE SUJA', 'EMENDA/REPARO CONDUTOR (DIR/UNI)',
       'JUMPER (DIR/UNI)', 'CORRO. GRAMPO SUSP. CONDUTOR (DIR/UNI)',
       'CORRO. GRAMPO SUSP. CONDUTOR (ESQ)', 'ESTRUTURA', 'INVASAO',
       'NINHO DE PÁSSARO', 'ESFERA (DIR/UNI)', 'RABICHO (ESQ)',
       'DISTANCIA DO CABO A VEGETACAO',
       'ISOL - I

In [ ]:
import re

def filter_text(text):
    # print(text)
    text = text.upper()
    
    # Filtro tokens inúteis
    # (?<=\s)NO( |$)|
    # (?<=\s)DO( |$)|
    # (?<=\s)E( |$)|
    # \.|(D:)
    # ()
    # espaços seguidos ou inúteis
    text = re.sub(r'(?<=\s)N(A|O)( |$)|(?<=\s)EM( |$)|(?<=\s)D(A|E|O)( |$)|(?<=\s)E( |$)|\.|(D:)|\/( |$)',' ', text)
    text = re.sub(r'\(|\)',' ', text)
    text = re.sub(r'(^\s+)|(\s{1,})(?=\s\S)|(\s+$)', '', text)
    
    # Fitro T**
    # ((?<=T)(\D|)(?=\d+))
    text = re.sub(fr'((?<=T)(\D|)(?=\d{1,}))', '', text)
    
    # Completar palavras cortadas padrão
    # Fases
    if match := re.search(r'((?<= )FASE\s)([A-Z]{1,}(?=\s|$))', text):
        fase = match.group(2)
        text = text[:match.span()[0]] + text[match.span()[1]:]
        # Match com as possiblidades
        if fase[0] == 'S':
            fase = 'SUPERIOR'
        elif fase[0] == 'M' or fase[0] == 'C':
            fase = 'MEIO'
        elif fase[0] == 'V':
            fase = 'VERMELHA'
        elif fase[0] == 'B':
            fase = 'BRANCA'
        elif len(fase) > 1:
            if fase[:2] == 'EX':
                fase = 'EXTERNA'
            elif fase[:2] == 'ES':
                fase = 'ESQUERDA'
            elif fase[:2] == 'DI':
                fase = 'DIREITA'
            elif len(fase) > 2:
                if fase[:2] == 'IN':
                    if fase[2] == 'F':
                        fase = 'INFERIOR'
                    elif len(fase) > 5:
                        if fase[5] == 'N':
                            fase = 'INTERNA'
                        elif fase[5] == 'M':
                            fase = 'INTERMEDIARIA'
        # inconclusiva => excluir
        else: fase = ''
        text = text + ' ' + fase
        
    # Lado
    if match := re.search(r'((?<= )LADO\s)([A-Z]{1,}(?=\s|$))', text):
        lado = match.group(2)
        text = text[:match.span()[0]] + text[match.span()[1]:]
        # Match com as possiblidades
        if lado[0] == 'V':
            lado = 'VIVO'
        elif lado[0] == 'M':
            lado = 'MORTO'
        elif len(lado) > 1:
            if lado[:2] == 'ES':
                lado = 'ESQUERDO'
            elif lado[:2] == 'DI':
                lado = 'DIREITO'
            elif lado[:2] == 'IN':
                lado = 'INFERIOR'
            elif lado[:2] == 'EN':
                lado = 'ENERGIZADO'
            elif lado[:2] == 'DE':
                lado = 'DESENERGIZADO'
        elif lado == 'CAV' or lado == 'CPV':
            lado = lado
        # inconclusiva => excluir
        else: lado = ''
        text = text + ' ' + lado
    
    # print(denom)
    # print(item)
    # print(text)
    return text

def empty_spaces(text):
    tags = re.split(r'\. |\/( |$)| | - ', text)
    
    for i in range(len(tags)):
        if tags[i] == None: continue
        # Remoção de ' ' duplicados e inúteis
        # só ta dando match no primeiro :(
        tags[i] = re.sub(r'(^\s+)|(\s{1,})(?=\s\S)|(\s+$)', '', tags[i])
    tags = list(filter(None, tags))
    print(tags)
    return tags

In [57]:
texts = dt.dropna().apply(lambda x: filter_text(x['text']), axis=1)

In [58]:
dt['text'].str.contains('ISOLADORE').value_counts()

text
False    327653
True          3
Name: count, dtype: int64

In [59]:
dt.dropna().loc[dt.dropna()['text'].str.contains(' lado d'), 'text'].unique()

array(['Cortar arbustos lado direito do vão',
       'Reabrir  faixa lado direito',
       'LT ARR-POF lado direito. fase inferior (',
       'Esfera corrida lado direito.',
       'Cortar/poda de árvores lado direito T12',
       'Cortar árvores na faixa lado direito T6',
       'Cortar eucaliptos lado direito/esquerdo',
       'Reabrir faixa lado direito T6',
       'Podar árvore lado direito com auxilio do',
       'Brotos de eucalipto lado direito da LT.',
       'Rabicho danificado lado direito (OPGW)',
       'Cavalote torto lado direito intermediari',
       'Cortar rebrotas de eucaliptos ao lado di',
       '2 isoladores do lado desenergizado para',
       'Parafusos chapa L fase superior lado dir',
       '1 eucalipto lado direito  e 2 no lado es',
       'Falta cupilha no cavalote. lado direito.',
       'Chapa duplicadora danificada. lado direi',
       'Abertura de faixa lado direito.',
       'Falta esfera no para raio lado direito',
       'Grampo lado direito vante com c

In [60]:
import spacy

if 'pt_core_news_sm' not in spacy.util.get_installed_models():
    spacy.cli.download('pt_core_news_sm')

# Tokenização
nlp = spacy.load('pt_core_news_sm')

In [61]:
tags = text.apply(lambda x: empty_spaces(x))

['ROÇADA', 'MECANIZADA', 'FINAL', 'VÃO', '50X30']
['ROÇADA', 'MANUAL', 'INÍCIO', 'VÃO', '180X30', 'R']
['ROÇADA', 'MECANIZADA', 'MEIO', 'FIM', 'VÃO', '1']
['ROÇADA', 'MANUAL', 'MEIO', 'FIM', 'VÃO', '200X3']
['ROÇADA', 'MECANIZADA', 'VÃO', 'TOTAL', '345X30', 'REL']
['ROÇADA', 'MANUAL', 'VÃO', 'TOTAL', '200X30', 'RELATIV']
['ROÇADA', 'MANUAL', 'INÍCIO', 'MEIO', 'VÃO', '20']
['ROÇADA', 'MECANIZADA', 'FINAL', 'VÃO', '120X25']
['ROÇADA', 'MANUAL', 'VÃO', 'TOTAL', '300X30', 'RELATIVO']
['ROÇADA', 'MANUAL', 'INÍCIO', 'MEIO', 'VÃO', '22']
['ROÇADA', 'MANUAL', 'INÍCIO', 'MEIO', 'VÃO', '20']
['ROÇADA', 'MANUAL', 'MEIO', 'VÃO', '70X30', 'RELA']
['ROÇADA', 'MANUAL', 'INÍCIO', 'VÃO', '50X30', 'RE']
['ROÇADA', 'MANUAL', 'VÃO', 'TOTAL', '350X30', 'RELATIVO']
['ROÇADA', 'MANUAL', 'VÃO', 'TOTAL', '150X30', 'RELATIVO']
['ROÇADA', 'MANUAL', 'INÍCIO', 'MEIO', 'VÃO', '20']
['ROÇADA', 'MANUAL', 'MEIO', 'FIM', 'VÃO', '100X3']
['PODAR', 'ÁRVORES', 'FAIXA', '50X30', 'AS', 'NECESSÁ']
['ROÇADA', 'MANUAL', 'MEIO'

In [62]:
tags

0               [ROÇADA, MECANIZADA, FINAL, VÃO, 50X30]
1              [ROÇADA, MANUAL, INÍCIO, VÃO, 180X30, R]
2               [ROÇADA, MECANIZADA, MEIO, FIM, VÃO, 1]
3               [ROÇADA, MANUAL, MEIO, FIM, VÃO, 200X3]
4         [ROÇADA, MECANIZADA, VÃO, TOTAL, 345X30, REL]
                              ...                      
344279                                              [5]
344281                                              [4]
344282          [FERRAGENS, CONDUTOR:FERRAGEM, CONECTO]
344283                 [0*1, 0*2, 0*3, 0*4, 2*5, 165*9]
344284        [TEMPERATURA:CONEXAO, 1*1, 0*2, 0*3, 0*4]
Length: 327656, dtype: object

In [63]:
unique_tags = list(set(x for y in tags for x in y))
temp = [x for y in tags for x in y]
count = dict((x, temp.count(x)) for x in unique_tags)

In [64]:
count

{'145*9': 7,
 'C': 87,
 'JUMPER:MAL': 16,
 'CERCA:SECCIONAMEN': 3,
 'FESTÕES': 1,
 'GALINHEIRO': 1,
 'DI': 98,
 'ARVORES': 23,
 '158*': 7,
 'ESTRUT': 5,
 'DESCARG': 2,
 'DISTAN': 91,
 '77': 1,
 'C/BAMBUS': 3,
 '88KV': 2,
 'PORTE': 8,
 'GUEDES': 94,
 '104': 1,
 'DANIFICAD': 1,
 '"COM': 1,
 'RAMAL': 3,
 'BANANEIRAS': 6,
 'MASTRO': 24,
 'PINHEIROS': 4,
 '15': 302,
 'BEIRA': 9,
 'CERC': 1,
 '141*9': 3,
 'ESPACADOR:': 118,
 'CERCA:ATER': 2,
 'SOBREAQUEC': 1,
 'NUMERAÇÃO': 68,
 '9.000': 1,
 'MANDÍBULA': 1,
 '35': 1,
 '135': 1,
 '41': 1,
 '(FASE': 1,
 'ÁRVOR': 1,
 'ROMPIDOS': 18,
 'ÁRV': 1,
 'TOR': 15,
 'ACESO:INEXISTENTE': 3,
 'T36': 74,
 '124': 2,
 'DANIFICAÇÃO': 1,
 '100X2M': 1,
 '(GAVIÃO)': 1,
 '"FALTANDO': 2,
 'PLCA': 2,
 '280': 1,
 'N°135': 1,
 '60X30': 2,
 'SOBREAQUE': 1,
 'BAMBU': 37,
 'MURETA': 15,
 'GAN': 1,
 'HORIZONTAL': 2,
 'FUTURO.': 9,
 'NOTA:': 2,
 '500X30': 1,
 'VEÍCULO': 6,
 '"AQUECIMENTO': 2,
 'SUPERIOR': 131,
 '4.2682926829%': 44,
 'TRATAMENTO': 1,
 'APROXIMADAMENTE': 1,
 

In [65]:
tokens = []
for doc in nlp.pipe(tags):
    tokens.append([token for token in doc])

ValueError: [E1041] Expected a string, Doc, or bytes as input, but got: <class 'list'>

In [ ]:

from spellchecker import SpellChecker

spell = SpellChecker(language='pt')
misspellings_counts = len(spell.unknown([token.text for token in doc if token.is_alpha]))
